# 0. Instalacja i importowanie modułów

##### 0.1. Ogólne

In [1]:
!pip install -r requirements.txt --user
!pip list

Package                            Version
---------------------------------- -------------------
absl-py                            0.12.0
alabaster                          0.7.12
anaconda-client                    1.7.2
anaconda-navigator                 1.10.0
anaconda-project                   0.8.3
argh                               0.26.2
argon2-cffi                        20.1.0
asn1crypto                         1.4.0
astroid                            2.4.2
astropy                            4.0.2
astunparse                         1.6.3
async-generator                    1.10
atomicwrites                       1.4.0
attrs                              20.3.0
autopep8                           1.5.4
Babel                              2.8.1
backcall                           0.2.0
backports.functools-lru-cache      1.6.1
backports.shutil-get-terminal-size 1.0.0
backports.tempfile                 1.0
backports.weakref                  1.0.post1
bcrypt                            

menuinst                           1.4.16
mistune                            0.8.4
mkl-fft                            1.2.0
mkl-random                         1.1.1
mkl-service                        2.3.0
mock                               4.0.2
more-itertools                     8.6.0
mpmath                             1.1.0
msgpack                            1.0.0
multipledispatch                   0.6.0
navigator-updater                  0.2.1
nbclient                           0.5.1
nbconvert                          6.0.7
nbformat                           5.0.8
nest-asyncio                       1.4.2
networkx                           2.5
nltk                               3.5
nose                               1.3.7
notebook                           6.1.4
numba                              0.51.2
numexpr                            2.7.1
numpy                              1.19.2
numpydoc                           1.1.0
oauthlib                           3.1.0
olefile          

In [2]:
import numpy as np
import tflearn
import tensorflow
import random
import json
import nltk

Instructions for updating:
non-resource variables are not supported in the long term
curses is not supported on this machine (please install/reinstall curses for an optimal experience)


##### 0.2. Angielski Stemmer: https://www.nltk.org/_modules/nltk/stem/lancaster.html

In [4]:
nltk.download('punkt')
from nltk.stem.lancaster import LancasterStemmer
stemmer_en = LancasterStemmer()

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\annad\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


##### 0.3. Polski Stemmer **(Docelowy)**: https://pypi.org/project/pystempel/

In [5]:
from stempel import StempelStemmer

stemmer_pl = StempelStemmer.default() #.polimorf() #jest lepsza?

Loading:  92%|██████████████████████████████████████████████████▋    | 2051427/2225192 [00:01<00:00, 1634466.61bytes/s]

# 1. Załadowanie plików **.json** z bazą słów

##### 1.1. Docelowa baza słów polskich do nauki modelu (10 rodzajów odp - PL)

In [6]:
with open("intents_pl.json", encoding='utf-8') as file:
    data_pl = json.load(file)

print(data_pl)

{'intents': [{'tag': 'greeting', 'patterns': ['Cześć', 'Elo', 'Jesteś?', 'Hej', 'Dzień dobry', 'Sup', 'Witam', 'Hejka', 'Hej!'], 'responses': ['Cześć!', 'Dobrze Cię widzieć!', 'Hej, w czym mogę pomóc?'], 'context_set': ''}, {'tag': 'goodbye', 'patterns': ['narazie', 'Do zobaczenia', 'Dowidzenia', 'Dobranoc', 'Miłego dnia'], 'responses': ['Do zobaczenia później', 'Mam nadzieję, że później pogadamy', 'Narazie!'], 'context_set': ''}, {'tag': 'age', 'patterns': ['Ile masz lat', 'Ile lat ma Janet', 'Wiek', 'Jak stara jesteś', 'jaki jest twój wiek', 'Wieko', 'urodziny'], 'responses': ['Mam kilka dni', 'Urodziłam się 17.03.2021'], 'context_set': ''}, {'tag': 'name', 'patterns': ['Jak masz na imię', 'Jak Cię zwą?', 'twoje imie?', 'Imie', 'Jak cię nazywać', 'Kim jesteś'], 'responses': ['Możesz mnie nazywać Janet!', 'Jestem Janet', 'Jestem Janet, twój ulubiony chatbot'], 'context_set': ''}, {'tag': 'goout', 'patterns': ['Czy chcesz gdzieś wyjść?', 'zrobimy coś razem?', 'pójdziemy gdzieś razem?']

##### 1.2. Skrócona baza słów (4 rodzaje odp - PL)

In [7]:
with open("intents_pl_short.json", encoding='utf-8') as file:
  data_pl_short = json.load(file)

print(data_pl_short)

{'intents': [{'tag': 'greeting', 'patterns': ['Cześć', 'Elo', 'Jesteś?', 'Hej', 'Dzień dobry', 'Sup'], 'responses': ['Cześć!', 'Dobrze Cię widzieć!', 'Hej, w czym mogę pomóc?'], 'context_set': ''}, {'tag': 'goodbye', 'patterns': ['narazie', 'Do zobaczenia', 'Dowidzenia', 'Dobranoc', 'Miłego dnia'], 'responses': ['Do zobaczenia później', 'Mam nadzieję, że później pogadamy', 'Narazie!'], 'context_set': ''}, {'tag': 'age', 'patterns': ['Ile masz lat', 'Ile lat ma Janet', 'Wiek', 'Jak stara jesteś', 'urodziny'], 'responses': ['Mam kilka dni', 'Urodziłam się 17.03.2021'], 'context_set': ''}, {'tag': 'name', 'patterns': ['Jak masz na imię', 'Jak Cię zwą?', 'twoje imie?', 'Imie', 'Jak cię nazywać', 'Kim jesteś'], 'responses': ['Możesz mnie nazywać Janet!', 'Jestem Janet', 'Jestem Janet, twój ulubiony chatbot'], 'context_set': ''}]}


##### 1.3. Testowa baza słów angielskich (6 rodzajów odp - EN)

In [8]:
with open("intents_en.json", encoding='utf-8') as file:
  data_en = json.load(file)

print(data_en)

{'intents': [{'tag': 'greeting', 'patterns': ['Hi', 'How are you', 'Is anyone there?', 'Hello', 'Good day', 'Whats up'], 'responses': ['Hello!', 'Good to see you again!', 'Hi there, how can I help?'], 'context_set': ''}, {'tag': 'goodbye', 'patterns': ['cya', 'See you later', 'Goodbye', 'I am Leaving', 'Have a Good day'], 'responses': ['Sad to see you go :(', 'Talk to you later', 'Goodbye!'], 'context_set': ''}, {'tag': 'age', 'patterns': ['how old', 'how old is tim', 'what is your age', 'how old are you', 'age?'], 'responses': ['I am 18 years old!', '18 years young!'], 'context_set': ''}, {'tag': 'name', 'patterns': ['what is your name', 'what should I call you', 'whats your name?'], 'responses': ['You can call me Tim.', "I'm Tim!", "I'm Tim aka Tech With Tim."], 'context_set': ''}, {'tag': 'shop', 'patterns': ['Id like to buy something', 'whats on the menu', 'what do you reccommend?', 'could i get something to eat'], 'responses': ['We sell chocolate chip cookies for $2!', 'Cookies ar

# 2. Przygotowanie danych do nauki modelu

In [9]:
words = []
labels = []
docs_x = []
docs_y = []

##### 2.1 Stworzenie tablicy ze wszystkimi możliwymi inputami użytkownika (+ labele)

In [10]:
for intent in data_pl["intents"]: #Loop przez cały json
  for pattern in intent["patterns"]: #loop przez wszystkie możliwe rodzaje przykładowego inputu użytkownika
    wrds = nltk.word_tokenize(pattern) #Tokenizing every word
    words.extend(wrds) #Add every single tokenized word
    docs_x.append(wrds) #Add the whole tokenized sentence
    docs_y.append(intent["tag"]) #Pattern x coresponds to the tag y. Potrzebne do ustalenia relacji słowa z odpowiedzią

  if intent["tag"] not in labels:
    labels.append(intent["tag"]) #Add the tag

In [11]:
words = [stemmer_pl.stem(w.lower()) for w in words if w not in "?"] #stemming -> take each word and bring it to the "root" form. Only the stemmed version of the word is important to us
words = sorted(list(set(words))) #Sorting

labels = sorted(labels) #sorting

training = []
output = []

out_empty = [0 for _ in range(len(labels))]

In [12]:
#Podgląd zmiennych
print(f"Words:\n{words}")
print(f"labels:\n{labels}")
print(f"docs_y:\n{docs_y}")
print(f"docs_x:\n{docs_x}")

Words:
['!', 'a', 'bo', 'chcieć', 'chodzić', 'co', 'coś', 'czec', 'czy', 'dlaczy', 'dnia', 'do', 'dobranoc', 'dobry', 'dowidzieć', 'dzień', 'elo', 'gra', 'grać', 'gć', 'hej', 'hejka', 'ile', 'imia', 'imie', 'jak', 'jaka', 'jaki', 'janet', 'jest', 'ki', 'lat', 'mieć', 'miłeon', 'muzy', 'na', 'narazie', 'nazywać', 'o', 'plany', 'poczekać', 'pójdziemy', 'raz', 'robić', 'się', 'star', 'supć', 'słuchać', 'słychać', 'teraa', 'to', 'twoj', 'twój', 'ty', 'urodziny', 'w', 'wiek', 'wieko', 'witać', 'wyjść', 'y', 'zobaczyć', 'zrobić', 'zwać', 'zła']
labels:
['age', 'angry', 'doing', 'game', 'goodbye', 'goout', 'greeting', 'music', 'name', 'why']
docs_y:
['greeting', 'greeting', 'greeting', 'greeting', 'greeting', 'greeting', 'greeting', 'greeting', 'greeting', 'goodbye', 'goodbye', 'goodbye', 'goodbye', 'goodbye', 'age', 'age', 'age', 'age', 'age', 'age', 'age', 'name', 'name', 'name', 'name', 'name', 'name', 'goout', 'goout', 'goout', 'doing', 'doing', 'doing', 'doing', 'game', 'game', 'game', '

##### 3.2. Przypisywanie słów do danej kategorii (ie. "Cześć" do Greetings)

W przypadku data_pl_short są tylko 4 rodzaje odpowiedzi. "Cześć" które zostane przypisane do labela "greeting" będzie miało formę końcowego outputu "1000" jeżeli label "greetings" jest pierwszy do wyboru.

Warto też dodać, że sieć neuronowa nie przyjmuje teksu. To jest główny powód czemu przypisujemy słowa do kategorii

In [13]:
for x, doc in enumerate(docs_x): #Przejście przez wszystkie słowa
  bag =[]

  wrds = [stemmer_pl.stem(w).lower() for w in doc] #podział wszystkich słów w danym zdaniu

  for w in words:
    if w in wrds:
      bag.append(1) #this word exist
    else:
      bag.append(0) #do not exist
    
  output_row = out_empty[:] #kopia
  output_row[labels.index(docs_y[x])] = 1

  training.append(bag) #dodajemy nowe wyrażenie zamienione na ciąg binarny
  output.append(output_row)

training = np.array(training) #Zbiór treningowy
output = np.array(output) #Zbiór outputów

In [20]:
len(training) #dla pl_short mamy 44 słowa

48


Loading: 100%|███████████████████████████████████████████████████████| 2225192/2225192 [00:20<00:00, 1720623.81bytes/s]

In [11]:
len(output[0]) #Które można przypisać do 4 kategorii

10

In [14]:
print(training)
print(output)

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 1]
 [0 0 0 ... 0 0 0]]
[[0 0 0 0 0 0 1 0 0 0]
 [0 0 0 0 0 0 1 0 0 0]
 [0 0 0 0 0 0 1 0 0 0]
 [0 0 0 0 0 0 1 0 0 0]
 [0 0 0 0 0 0 1 0 0 0]
 [0 0 0 0 0 0 1 0 0 0]
 [0 0 0 0 0 0 1 0 0 0]
 [0 0 0 0 0 0 1 0 0 0]
 [0 0 0 0 0 0 1 0 0 0]
 [0 0 0 0 1 0 0 0 0 0]
 [0 0 0 0 1 0 0 0 0 0]
 [0 0 0 0 1 0 0 0 0 0]
 [0 0 0 0 1 0 0 0 0 0]
 [0 0 0 0 1 0 0 0 0 0]
 [1 0 0 0 0 0 0 0 0 0]
 [1 0 0 0 0 0 0 0 0 0]
 [1 0 0 0 0 0 0 0 0 0]
 [1 0 0 0 0 0 0 0 0 0]
 [1 0 0 0 0 0 0 0 0 0]
 [1 0 0 0 0 0 0 0 0 0]
 [1 0 0 0 0 0 0 0 0 0]
 [0 0 0 0 0 0 0 0 1 0]
 [0 0 0 0 0 0 0 0 1 0]
 [0 0 0 0 0 0 0 0 1 0]
 [0 0 0 0 0 0 0 0 1 0]
 [0 0 0 0 0 0 0 0 1 0]
 [0 0 0 0 0 0 0 0 1 0]
 [0 0 0 0 0 1 0 0 0 0]
 [0 0 0 0 0 1 0 0 0 0]
 [0 0 0 0 0 1 0 0 0 0]
 [0 0 1 0 0 0 0 0 0 0]
 [0 0 1 0 0 0 0 0 0 0]
 [0 0 1 0 0 0 0 0 0 0]
 [0 0 1 0 0 0 0 0 0 0]
 [0 0 0 1 0 0 0 0 0 0]
 [0 0 0 1 0 0 0 0 0 0]
 [0 0 0 1 0 0 0 0 0 0]
 [0 0 0 1 0 0 0 0 0 0]
 [0 0 

Loading: 100%|███████████████████████████████████████████████████████| 2225192/2225192 [00:20<00:00, 1634466.61bytes/s]

# 3. Model i jego ćwiczenie

In [15]:
training = np.array(training) #zamiana typu dla sieci neuronowej
output = np.array(output) #zamiana typu dla sieci neuronowej

##### 3.1. Stworzenie DLN i inicjacja modelu

In [16]:
tensorflow.compat.v1.reset_default_graph() #Reset na wszelki wypadek (w sumie nie wiem czy to jakaś super ważna linijka kodu)

net = tflearn.input_data(shape=[None, len(training[0])]) #Input layer
net = tflearn.fully_connected(net, 8) #8 neurons for hidden layer
net = tflearn.fully_connected(net, 8) #8 neurons for hidden layer
#net = tflearn.fully_connected(net, 8) #8 neurons for hidden layer
net = tflearn.fully_connected(net, len(output[0]), activation="softmax") #len(output) neurons for output layer + Softmax jako najlepsze wyjście dla tego typu danych
net = tflearn.regression(net)

model = tflearn.DNN(net)



Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


##### 3.2. Trening Modelu

In [17]:
model.fit(training, output, n_epoch=1000, batch_size=8, show_metric=True)

#Zapis Modelu
model.save("model.tflearn")

Training Step: 5999  | total loss: 0.02785 | time: 0.007s
| Adam | epoch: 1000 | loss: 0.02785 - acc: 0.9753 -- iter: 40/48
Training Step: 6000  | total loss: 0.02583 | time: 0.008s
| Adam | epoch: 1000 | loss: 0.02583 - acc: 0.9777 -- iter: 48/48
--
INFO:tensorflow:C:\Users\annad\Desktop\System Dialogowy Janet\model.tflearn is not in all_model_checkpoint_paths. Manually adding it.


# 4. Input Użytkownika

##### 4.1 Funkcja **"bag_of_words(s, words)"** do stemmowania twojego zdania, i przypisania mu formy binarnej

In [18]:
def bag_of_words(s, words):
  bag = [0 for _ in range(len(words))]

  s_words = nltk.word_tokenize(s)
  s_words = [stemmer_pl.stem(word.lower()) for word in s_words]

  for se in s_words:
    for i, w in enumerate(words):
      if w == se:
        bag[i] = 1
  return np.array(bag)

##### 4.2 Funkcja **"chat()"** do rozmowy z botem

In [19]:
def chat():
  print("Możesz rozpocząć rozmowę z Botem! (type quit to stop)")
  while True: #Ciągła rozmowa
    inp = input("Ty: ")
    if inp.lower() == "quit": #Quit by wyjść z loopa
      break

    result = model.predict([bag_of_words(inp,words)]) #Predictowanie przy pomocy wyćwiczonego modelu
    result_index = np.argmax(result)
    tag = labels[result_index]
    
    for tg in data_pl["intents"]: #znalezienie poprawnego tagu do zdania
      if tg['tag'] == tag:
        responses = tg['responses']
      
    print(random.choice(responses)) #Wyprintuj losową odpowiedz z danego zbioru odpowiedzi

# 5. Rozmowa z botem!

In [ ]:
chat()

Możesz rozpocząć rozmowę z Botem! (type quit to stop)
Ty: elo
Cześć!
Ty: w co grasz
W OSRS
Ty: nara
Hej, w czym mogę pomóc?
Ty: narazie
Narazie!
Ty: do widzenia
Mam nadzieję, że później pogadamy
Ty: dowidzenia
Narazie!
Ty: ok
Hej, w czym mogę pomóc?
